### Import reviews

In [3]:
%load_ext autoreload
%autoreload 2

import progressbar

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [4]:
import pickle

DATA_FILE1 = 'data/data.pkl'
DATA_FILE2 = 'data/labels.pkl'

with open(DATA_FILE1, 'rb') as f:
    reviews = pickle.load(f)
    
with open(DATA_FILE2, 'rb') as f:
    labels = pickle.load(f)

In [5]:
print(len(reviews[0]))
print(len(labels[0]))

20959
20959


In [6]:
from babble.babbler import BabbleStream

babbler = BabbleStream(reviews,labels,balanced=True, shuffled=True, seed=456)

Grammar construction complete.


In [7]:
from babble.utils import display_candidate

candidate = babbler.next()
print(candidate)
print(candidate.text)
print(candidate.entity_positions)

RelationMention(doc_id=21119: entities=("experience"(10:20), "car"(26:29), "company"(37:44))
the worst experience with car rental company. .they have only one representative i had 5 people before me and i waited for 2 hours to get the car rental. ..if u could i was give them 0 syar
[(10, 20), (26, 29), (37, 44)]


In [8]:
import re

def get_words_before(quantity,sentence,entity):
    sentence = re.sub(r'[^\w\s]','',sentence)
    words = sentence.split()
    if entity in words:
        index = words.index(entity)
        before = index - min(index, quantity)
        return ' '.join(map(str, words[before:index])) 

In [9]:
import re

def get_words_after(quantity,sentence,entity):
    sentence = re.sub(r'[^\w\s]','',sentence)
    words = sentence.split()
    if entity in words:
        index = words.index(entity) +1
        after = index + min(index, quantity)
        return ' '.join(map(str, words[index:after]))

In [10]:
from nltk.sentiment.vader import SentimentIntensityAnalyzer

sid = SentimentIntensityAnalyzer()

pos_adjectives_list=[]
neu_adjectives_list=[]
neg_adjectives_list=[]

def check_sentiment_adjective(adjective):
    if (sid.polarity_scores(adjective)['compound']) >= 0.1:
        pos_adjectives_list.append(adjective)
        return 'positive'
    elif (sid.polarity_scores(adjective)['compound']) <= -0.1:
        neg_adjectives_list.append(adjective)
        return 'negative'
    else:
        neu_adjectives_list.append(adjective)
        return 'neutral' 

In [11]:
def check_adjectives_before_pos(sentence,entity):
    words = get_words_before(2,sentence,entity)
    if words == None or len(words.split(" ")) == 0:
        return None
    else:
        spacy_nlp = spacy.load('en_core_web_sm')
        doc = spacy_nlp(words)
        for token in doc:
            if token.pos_ == 'ADJ':
                return token.text
                break

In [12]:
def check_adjectives_after_verb(sentence,entity):
    words = get_words_after(3,sentence,entity)
    if words == None or len(words.split(" ")) < 3:
        return None
    else:
        spacy_nlp = spacy.load('en_core_web_sm')
        doc = spacy_nlp(words)
        if doc[0].pos_ == 'VERB' and (doc[1].pos_ == 'ADJ' or doc[2].pos_ == 'ADJ'):
            return doc[1].text

In [13]:
import spacy

spacy_stopwords = spacy.lang.en.stop_words.STOP_WORDS

print('spaCy Version: %s' % (spacy.__version__))
spacy_nlp = spacy.load('en_core_web_sm')

spaCy Version: 2.1.8


In [14]:
from babble import Explanation

explanations = []
index = 1


for candidate,label in progressbar.progressbar(zip(reviews[0],labels[0])):
#    print(candidate.text)
    doc = spacy_nlp(candidate.text)
    for token in doc:
        if token.pos_ == 'ADJ':
            adjective = token.text
            explanation = Explanation(
            name='LF_' + str(index),
            label=label,
            condition='the word "' + adjective + '" is in the sentence',
            candidate=candidate,
            )
            explanations.append(explanation)
            index = index + 1
#            print(str(explanation).upper())

| |                                     #         | 20958 Elapsed Time: 0:04:26


In [15]:
for explanation in explanations:
    print(explanation.candidate)

RelationMention(doc_id=1: entities=("bill"(6:10), "service"(29:36), "charge"(88:94))
RelationMention(doc_id=1: entities=("bill"(6:10), "service"(29:36), "charge"(88:94))
RelationMention(doc_id=2: entities=("love"(0:4), "place"(10:15), "downtown"(16:24))
RelationMention(doc_id=3: entities=("place"(6:11), "staff"(13:18), "help"(71:75))
RelationMention(doc_id=3: entities=("place"(6:11), "staff"(13:18), "help"(71:75))
RelationMention(doc_id=3: entities=("place"(6:11), "staff"(13:18), "help"(71:75))
RelationMention(doc_id=4: entities=("idea"(10:14), "owner"(24:29), "problem"(32:39))
RelationMention(doc_id=4: entities=("idea"(10:14), "owner"(24:29), "problem"(32:39))
RelationMention(doc_id=4: entities=("idea"(10:14), "owner"(24:29), "problem"(32:39))
RelationMention(doc_id=4: entities=("idea"(10:14), "owner"(24:29), "problem"(32:39))
RelationMention(doc_id=4: entities=("idea"(10:14), "owner"(24:29), "problem"(32:39))
RelationMention(doc_id=4: entities=("idea"(10:14), "owner"(24:29), "problem

RelationMention(doc_id=1018: entities=("experience"(10:20), "life"(27:31), "cut"(33:36))
RelationMention(doc_id=1018: entities=("experience"(10:20), "life"(27:31), "cut"(33:36))
RelationMention(doc_id=1018: entities=("experience"(10:20), "life"(27:31), "cut"(33:36))
RelationMention(doc_id=1019: entities=("time"(4:8), "waitress"(53:61), "return"(111:117))
RelationMention(doc_id=1020: entities=("shame"(0:5), "parking"(29:36), "north"(149:154))
RelationMention(doc_id=1020: entities=("shame"(0:5), "parking"(29:36), "north"(149:154))
RelationMention(doc_id=1020: entities=("shame"(0:5), "parking"(29:36), "north"(149:154))
RelationMention(doc_id=1020: entities=("shame"(0:5), "parking"(29:36), "north"(149:154))
RelationMention(doc_id=1021: entities=("sub"(0:3), "par"(4:7), "waitress"(21:29))
RelationMention(doc_id=1022: entities=("hour"(48:52), "wait"(56:60), "order"(70:75))
RelationMention(doc_id=1023: entities=("customer"(45:53), "business"(109:117), "mistake"(201:208))
RelationMention(doc_i

RelationMention(doc_id=2060: entities=("cheese"(14:20), "pizza"(45:50), "pizza"(74:79))
RelationMention(doc_id=2060: entities=("cheese"(14:20), "pizza"(45:50), "pizza"(74:79))
RelationMention(doc_id=2060: entities=("cheese"(14:20), "pizza"(45:50), "pizza"(74:79))
RelationMention(doc_id=2060: entities=("cheese"(14:20), "pizza"(45:50), "pizza"(74:79))
RelationMention(doc_id=2060: entities=("cheese"(14:20), "pizza"(45:50), "pizza"(74:79))
RelationMention(doc_id=2061: entities=("customer"(6:14), "service"(15:22), "counter"(72:79))
RelationMention(doc_id=2061: entities=("customer"(6:14), "service"(15:22), "counter"(72:79))
RelationMention(doc_id=2061: entities=("customer"(6:14), "service"(15:22), "counter"(72:79))
RelationMention(doc_id=2061: entities=("customer"(6:14), "service"(15:22), "counter"(72:79))
RelationMention(doc_id=2061: entities=("customer"(6:14), "service"(15:22), "counter"(72:79))
RelationMention(doc_id=2061: entities=("customer"(6:14), "service"(15:22), "counter"(72:79))
Re

RelationMention(doc_id=3003: entities=("cleaning"(42:50), "job"(51:54), "room"(59:63))
RelationMention(doc_id=3003: entities=("cleaning"(42:50), "job"(51:54), "room"(59:63))
RelationMention(doc_id=3003: entities=("cleaning"(42:50), "job"(51:54), "room"(59:63))
RelationMention(doc_id=3004: entities=("bar"(12:15), "review"(27:33), "bartender"(53:62))
RelationMention(doc_id=3004: entities=("bar"(12:15), "review"(27:33), "bartender"(53:62))
RelationMention(doc_id=3005: entities=("nail"(5:9), "spa"(10:13), "country"(41:48))
RelationMention(doc_id=3006: entities=("dr"(0:2), "eye"(30:33), "doctor"(34:40))
RelationMention(doc_id=3006: entities=("dr"(0:2), "eye"(30:33), "doctor"(34:40))
RelationMention(doc_id=3006: entities=("dr"(0:2), "eye"(30:33), "doctor"(34:40))
RelationMention(doc_id=3007: entities=("star"(4:8), "repair"(108:114), "court"(165:170))
RelationMention(doc_id=3007: entities=("star"(4:8), "repair"(108:114), "court"(165:170))
RelationMention(doc_id=3007: entities=("star"(4:8), "r

RelationMention(doc_id=3921: entities=("car"(116:119), "insurance"(133:142), "process"(168:175))
RelationMention(doc_id=3923: entities=("phone"(15:20), "day"(41:44), "way"(54:57))
RelationMention(doc_id=3923: entities=("phone"(15:20), "day"(41:44), "way"(54:57))
RelationMention(doc_id=3923: entities=("phone"(15:20), "day"(41:44), "way"(54:57))
RelationMention(doc_id=3923: entities=("phone"(15:20), "day"(41:44), "way"(54:57))
RelationMention(doc_id=3924: entities=("star"(7:11), "stop"(40:44), "pm"(71:73))
RelationMention(doc_id=3924: entities=("star"(7:11), "stop"(40:44), "pm"(71:73))
RelationMention(doc_id=3924: entities=("star"(7:11), "stop"(40:44), "pm"(71:73))
RelationMention(doc_id=3925: entities=("town"(17:21), "try"(70:73), "pizza"(77:82))
RelationMention(doc_id=3926: entities=("delivery"(41:49), "sushi"(65:70), "piece"(90:95))
RelationMention(doc_id=3926: entities=("delivery"(41:49), "sushi"(65:70), "piece"(90:95))
RelationMention(doc_id=3926: entities=("delivery"(41:49), "sushi

...

RelationMention(doc_id=14425: entities=("favorite"(3:11), "sushi"(12:17), "spot"(18:22))
RelationMention(doc_id=14426: entities=("service"(9:16), "plenty"(49:55), "cream"(59:64))
RelationMention(doc_id=14426: entities=("service"(9:16), "plenty"(49:55), "cream"(59:64))
RelationMention(doc_id=14426: entities=("service"(9:16), "plenty"(49:55), "cream"(59:64))
RelationMention(doc_id=14427: entities=("idea"(80:84), "cuisine"(106:113), "downtown"(117:125))
RelationMention(doc_id=14427: entities=("idea"(80:84), "cuisine"(106:113), "downtown"(117:125))
RelationMention(doc_id=14427: entities=("idea"(80:84), "cuisine"(106:113), "downtown"(117:125))
RelationMention(doc_id=14427: entities=("idea"(80:84), "cuisine"(106:113), "downtown"(117:125))
RelationMention(doc_id=14428: entities=("music"(6:11), "good"(12:16), "food"(17:21))
RelationMention(doc_id=14428: entities=("music"(6:11), "good"(12:16), "food"(17:21))
RelationMention(doc_id=14428: entities=("music"(6:11), "good"(12:16), "food"(17:21))
Re

RelationMention(doc_id=15003: entities=("atmosphere"(6:16), "yelp"(33:37), "customer"(93:101))
RelationMention(doc_id=15004: entities=("food"(0:4), "kind"(25:29), "favorite"(122:130))
RelationMention(doc_id=15004: entities=("food"(0:4), "kind"(25:29), "favorite"(122:130))
RelationMention(doc_id=15004: entities=("food"(0:4), "kind"(25:29), "favorite"(122:130))
RelationMention(doc_id=15004: entities=("food"(0:4), "kind"(25:29), "favorite"(122:130))
RelationMention(doc_id=15004: entities=("food"(0:4), "kind"(25:29), "favorite"(122:130))
RelationMention(doc_id=15004: entities=("food"(0:4), "kind"(25:29), "favorite"(122:130))
RelationMention(doc_id=15005: entities=("menu"(11:15), "lunch"(29:34), "seating"(102:109))
RelationMention(doc_id=15005: entities=("menu"(11:15), "lunch"(29:34), "seating"(102:109))
RelationMention(doc_id=15005: entities=("menu"(11:15), "lunch"(29:34), "seating"(102:109))
RelationMention(doc_id=15005: entities=("menu"(11:15), "lunch"(29:34), "seating"(102:109))
Relatio

RelationMention(doc_id=15615: entities=("fish"(0:4), "bean"(32:36), "burrito"(37:44))
RelationMention(doc_id=15615: entities=("fish"(0:4), "bean"(32:36), "burrito"(37:44))
RelationMention(doc_id=15615: entities=("fish"(0:4), "bean"(32:36), "burrito"(37:44))
RelationMention(doc_id=15615: entities=("fish"(0:4), "bean"(32:36), "burrito"(37:44))
RelationMention(doc_id=15615: entities=("fish"(0:4), "bean"(32:36), "burrito"(37:44))
RelationMention(doc_id=15616: entities=("brisket"(6:13), "mouth"(27:32), "butter"(38:44))
RelationMention(doc_id=15617: entities=("food"(26:30), "dressing"(66:74), "service"(115:122))
RelationMention(doc_id=15617: entities=("food"(26:30), "dressing"(66:74), "service"(115:122))
RelationMention(doc_id=15617: entities=("food"(26:30), "dressing"(66:74), "service"(115:122))
RelationMention(doc_id=15617: entities=("food"(26:30), "dressing"(66:74), "service"(115:122))
RelationMention(doc_id=15617: entities=("food"(26:30), "dressing"(66:74), "service"(115:122))
RelationMe

RelationMention(doc_id=16239: entities=("time"(53:57), "favorite"(72:80), "car"(81:84))
RelationMention(doc_id=16239: entities=("time"(53:57), "favorite"(72:80), "car"(81:84))
RelationMention(doc_id=16239: entities=("time"(53:57), "favorite"(72:80), "car"(81:84))
RelationMention(doc_id=16240: entities=("vegas"(33:38), "spot"(82:86), "time"(93:97))
RelationMention(doc_id=16240: entities=("vegas"(33:38), "spot"(82:86), "time"(93:97))
RelationMention(doc_id=16241: entities=("try"(0:3), "pizza"(18:23), "delivery"(60:68))
RelationMention(doc_id=16241: entities=("try"(0:3), "pizza"(18:23), "delivery"(60:68))
RelationMention(doc_id=16242: entities=("breakfast"(20:29), "toast"(99:104), "sausage"(114:121))
RelationMention(doc_id=16242: entities=("breakfast"(20:29), "toast"(99:104), "sausage"(114:121))
RelationMention(doc_id=16242: entities=("breakfast"(20:29), "toast"(99:104), "sausage"(114:121))
RelationMention(doc_id=16242: entities=("breakfast"(20:29), "toast"(99:104), "sausage"(114:121))
Re

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
print(explanations)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [17]:
from babble.utils import ExplanationIO

FILE = "data/my_explanations.tsv"
exp_io = ExplanationIO()
exp_io.write(explanations, FILE)
explanations = exp_io.read(FILE)

Wrote 97499 explanations to data/my_explanations.tsv
Read 97499 explanations from data/my_explanations.tsv
